# ***AccessViz Mapper - Helsinki Region***
The AccessViz Mapper is a tool which let analyze the Accessibility Travel Times by different Transport Mode in the Helsinki Region. As a user, you have to select the YKR IDs of the grids you want to analyze. Then, you interact with the web app to create shapefiles/geopackage files and/or to visualize maps. 
With AccessViz Mapper you can:
- Download as shp/gpkg files with Travel Times info from selected YKR Grids
- Visualize/download maps of Travel Times
- Downloads as shp/gpkg files with Travel Times Comparison by Transport Mode
- Visualize/download maps of Travel Times Comparison by Transport Mode
- Download Shortest Path(s) as shp/gpkg from selected YKR Grids by selected Path Network
- Visualize/download maps of Shortest Path(s) from selected YKR Grids by selected Path Network

Take a look the **YKR ID Explorer** at the end of the web map to choose properly the YKR IDs

***Follow the next steps and discover the Accessibility at Helsinki Region***

## ***1. File Finder***
________________________
Type and/or select the YKR IDs you want to analyze Accessibility. Try some YKR IDs in sample data like: `5963655`, `5925860`, `5933038`. 

In [44]:
import folium
from pyproj import CRS
import geopandas as gpd
import pandas as pd
import matplotlib.pyplot as plt
import glob
import os
import numpy as np

In [45]:
# -----------------------------------------------------------------------------
#                                   FUNCTIONS
# -----------------------------------------------------------------------------
def read_grid(path):
    import geopandas as gpd
    '''
    Def which gives back the YKR Grid in WGS84
    ------------------------------------------
    PARAMETERS
     - path <URL>

    RETURNS
    - grid <GeoDataFrame>
    ------------------------------------------
    '''

    # reading grid with geopandas
    grid = gpd.read_file(path)

    # projecting grid to WGS84
    grid = grid.to_crs(4326)

    return grid


def on_button_clicked(b):
    '''
    Def used to append and print in display the selected YKR IDs
    ------------------------------------------------------------
    PARAMETERS
    - b <button default>

    RETURNS
    - Automatic append of selected YKR IDs <list element> (global variable)
    - Message in display
    '''

    if select_id.value not in grid_ids:
        if select_id.value != '':
            grid_ids.append(select_id.value)

        with out:
            return print('Selected YKR IDs: {}'.format(grid_ids))


def on_button_clear(c):
    '''
    Def used to clear selected YKR IDs
    -----------------------------------
    PARAMETERS
    -c <default button>

    RETURNS
    - automatic empty list (global variable)
    - Message in display
    '''

    # clear global variable of selected YKR IDs
    grid_ids.clear()

    with out:
        clear_output()
        return print('Selected YKR IDs: {}'.format(grid_ids))

In [46]:
# --------------------------------------------------------------------------------------
# SETTING - READING THE YKR GRID DATA FOR TRAVEL TIMES IN HELSINKI REGION
# --------------------------------------------------------------------------------------

# home folder
home_folder = os.getcwd()

# local downloads folder
local_folder_default = os.path.join(home_folder, 'downloads')
if not os.path.exists(local_folder_default):
    os.makedirs(local_folder_default)

# reading Grid with Grid path
grid_path = os.path.join(home_folder,'data\MetropAccess_YKR_grid_EurefFIN.shp')

# folder path
ykr_folder = os.path.join(home_folder, 'data\HelsinkiTravelTimeMatrix2018')

# definying Grid with function
grid = read_grid(grid_path)

In [47]:
import ipywidgets as widgets
from IPython.display import display, clear_output
from ipywidgets import jslink
from __future__ import print_function

In [48]:
# creating the List which includes all the YKR IDs
grid['YKR_ID'] = grid['YKR_ID'].astype(str)

grid_list = grid['YKR_ID'].to_list()

# definying a new empty list with the selected YKR IDs
grid_ids = []

# --------------------------------------------------------------------------------------------

# adding the combobox widget. Combobox means that you can type and select the correct one.
select_id = widgets.Combobox(placeholder='Type/select the YKR ID', 
                             options=grid_list, description='YKR ID:',
                             ensure_option=True, 
                             disabled=False)

# adding the button widget. Click Me Tooltip is an action which run after clicking on the button.
b = widgets.Button(description='Add YKR ID', 
                   disabled=False, 
                   button_style='info', 
                   tooltip='Click me', 
                   icon='check')

c = widgets.Button(description='Clear selection', 
                   disabled=False, 
                   button_style='danger', 
                   tooltip='Click me', 
                   icon='remove')

# --------------------------------------------------------------------------------------------

# output variable is used to display in rendering the selected variable
out = widgets.Output()
        
# adding the click event to the button. To add event you do it as a function
b.on_click(on_button_clicked)
c.on_click(on_button_clear)

# ------ TO DISPLAY -------

display(select_id)
display(b)
display(c)
display(out)

Combobox(value='', description='YKR ID:', ensure_option=True, options=('5785640', '5785641', '5785642', '57856…

Button(button_style='info', description='Add YKR ID', icon='check', style=ButtonStyle(), tooltip='Click me')

Button(button_style='danger', description='Clear selection', icon='remove', style=ButtonStyle(), tooltip='Clic…

Output()

## ***2. Table Joiner***
________________________
Table Joiner add the information of Travel Times to your selected YKR IDs and download in a local folder. There is a default `downloads` folder created at the repository or you can `type the URL of your selected local folder`. **Note:** do not erase the URL of the Text Box while using the AccessViz Mapper. You need to download the files in order to visualize them.

In [49]:
# -----------------------------------------------------------------------------
#                                   FUNCTIONS
# -----------------------------------------------------------------------------
def create_ykr_files_list(list_of_ids):
    '''
    Def used to create a list of URLs with a selected list of YKR Ids
    -----------------------------------------------------------------
    :param
    - list_of_ids: <list>
    the global variable is called grid_ids <list>

    :return:
    - ykr_files_list: <list> contains list of URLs of local files with Travel Times
    '''
    ykr_files_list = []

    for grid_name in list_of_ids:

        # find the folder of the selected YKR ID
        folder_id = grid_name[:4] + 'xxx'

        # find the table name of the selected YKR ID
        table_id = 'travel_times_to_ {}.txt'.format(grid_name)

        # create the url of the selected YKR ID
        url_file = os.path.join(ykr_folder, '{}\{}'.format(folder_id, table_id))

        # append the urls to a list
        ykr_files_list.append(url_file)

    return ykr_files_list


def save_as_shp(list_all_ykr_files, list_len_of_list, url_button):
    '''
    Def which saves as SHP file the selected YKR IDs in the Dashboard
    -----------------------------------------------------------------
    :param
    - list_all_ykr_files: <list> list with url tables with Travel Times

    - list_len_of_list: <list> list with the len number of each element
       defined as list(range(len(ykr_files_list)))

    - url_button: <widget button (tex input)>
      Text Box that contains the URL folder to save shp files

    :return:
    - automatic saving in specified folder
    '''

    with save_out:
        clear_output()

    # iterating over files
    for ykr_file, n in zip(list_all_ykr_files, list_len_of_list):

        # reading travel times table
        data = pd.read_csv(ykr_file, sep=';')

        # code as str
        data['from_id'] = data['from_id'].astype(str)

        with save_out:
            print('Joining... {}/{}'.format(n + 1, len(list_all_ykr_files)))

        # reading YKR Grid with function
        grid = read_grid(grid_path)
        grid['YKR_ID'] = grid['YKR_ID'].astype(str)

        # joining Travel Time data between YKR Grid and Travel Time table
        grid = grid.merge(data, left_on='YKR_ID', right_on='from_id')

        # handling empty values
        grid = grid.replace(-1, np.nan).dropna()

        # find the table name of the selected YKR ID
        table_name = os.path.basename(ykr_file)

        # defines URL to save the SHP
        shp_url = os.path.join(url_button.value, '{}'.format(table_name[:-4]) + '.shp')

        with save_out:
            print('Saving... {}/{}'.format(n + 1, len(list_all_ykr_files)))

        # saving selected YKR ID as SHP file with Travel Times
        grid.to_file(shp_url)

        with save_out:
            print('Saved in: {}\n'.format(shp_url))


def save_as_gpkg(list_all_ykr_files, list_len_of_list, url_button):
    '''
    Def which saves as GPKG file the selected YKR IDs in the Dashboard
    -----------------------------------------------------------------
    :param
    - list_all_ykr_files: <list> list with url tables with Travel Times

    - list_len_of_list: <list> list with the len number of each element
       defined as list(range(len(ykr_files_list)))

    - url_button: <widget button (tex input)>
      Text Box that contains the URL folder to save shp files

    :return:
    - automatic saving in specified folder
    '''

    with save_out:
        clear_output()

    # iterating over files
    for ykr_file, n in zip(list_all_ykr_files, list_len_of_list):

        # reading travel times table
        data = pd.read_csv(ykr_file, sep=';')

        # code as str
        data['from_id'] = data['from_id'].astype(str)

        with save_out:
            print('Joining... {}/{}'.format(n + 1, len(list_all_ykr_files)))

        # reading YKR Grid with function
        grid = read_grid(grid_path)
        grid['YKR_ID'] = grid['YKR_ID'].astype(str)

        # joining Travel Time data between YKR Grid and Travel Time table
        grid = grid.merge(data, left_on='YKR_ID', right_on='from_id')

        # handling empty values
        grid = grid.replace(-1, np.nan).dropna()

        # find the table of the selected YKR ID
        table_name = os.path.basename(ykr_file)

        # defines URL to save the GPKG
        gpkg_url = os.path.join(url_button.value, '{}'.format(table_name[:-4]) + '.gpkg')

        with save_out:
            print('Saving... {}/{}'.format(n + 1, len(list_all_ykr_files)))

        # saving selected YKR ID as SHP file with Travel Times
        grid.to_file(gpkg_url, driver="GPKG")

        with save_out:
            print('Saved in: {}\n'.format(gpkg_url))


def save_shp_button_clicked(shp_button):
    '''
    Def used to Activate the button to save the selected YKR IDs as Shapefiles
    --------------------------------------------------------------------------
    :param
    - shp_button: <widget button with click on event>

    :return
    Automatic saves files as SHP
    '''

    # getting the list of urls of the files to save
    ykr_files_list = create_ykr_files_list(grid_ids)

    # numerating the list of files
    n_list = list(range(len(ykr_files_list)))

    # save as shp with SHP FUNCTION
    save_as_shp(ykr_files_list, n_list, user_url)


def save_gpkg_button_clicked(gpkg_button):
    '''
    Def used to Activate the button to save the selected YKR IDs as Geopackage
    --------------------------------------------------------------------------
    :param
    - gpkg_button: <widget button with click on event>

    :return
    Automatic saves files as GPKG
    '''

    # getting the list of urls of the files to save
    ykr_files_list = create_ykr_files_list(grid_ids)

    # numerating the list of files
    n_list = list(range(len(ykr_files_list)))

    # save as shp with GPKG FUNCTION
    save_as_gpkg(ykr_files_list, n_list, user_url)

In [50]:
# --------------------------------------------------------------------------------------------

# adding a text box so the user can enter the url wanted to saved the joined files
user_url = widgets.Text(value = local_folder_default,
                        placeholder='Enter URL', 
                        description='Local folder:', 
                        disabled=False, 
                        continuous_update=True)

# adding a button widget to download as shp or gpkg. Tooltip is an action which run after click on the button.
shp_button = widgets.Button(description='Save as SHP', 
                            disabled=False, 
                            button_style='primary', 
                            tooltip='Click me', 
                            icon='download')

gpkg_button = widgets.Button(description='Save as GPKG', 
                            disabled=False, 
                            button_style='primary', 
                            tooltip='Click me', 
                            icon='download')

# --------------------------------------------------------------------------------------------

# output variable is used to display in rendering the selected variable
save_out = widgets.Output()
            
# adding the click event to the button. To add event you do it as a function
shp_button.on_click(save_shp_button_clicked)
gpkg_button.on_click(save_gpkg_button_clicked)


# ------ TO DISPLAY -------
display(user_url)
display(shp_button)
display(gpkg_button)
display(save_out)

Text(value='C:\\Users\\Bryan\\HELSINKI\\4. AutoGIS\\final project\\final-assignment-bryanvallejo16\\downloads'…

Button(button_style='primary', description='Save as SHP', icon='download', style=ButtonStyle(), tooltip='Click…

Button(button_style='primary', description='Save as GPKG', icon='download', style=ButtonStyle(), tooltip='Clic…

Output()

## ***3. Visualizer***
________________________
Choose the desired Tranport Mode, the Classification Scheme, the Color Map, Transparency (alpha), Number of Classes. Then, visualize/download the Map of Travel Times of Helsinki. 

In [51]:
import contextily as ctx
import mapclassify

In [52]:
# -----------------------------------------------------------------------------
#                                   FUNCTIONS
# -----------------------------------------------------------------------------

def read_sea():
    '''
    Def which gives back a sea layer from local data folder in respository
    ----------------------------------------------------------------------
    :returns
    - sea <GeoDataFrame>
    '''

    # defines sea path url  and reading
    sea_path = os.path.join(home_folder, 'data\sea.shp')
    sea = gpd.read_file(sea_path)

    return sea


def ykr_grid_code(ykr_file_path):
    '''
    Def which gives back the YKR GRID code of a selected file url
    -------------------------------------------------------------
    :param
    - ykr_file_path <url of SHP or GPKG>
    this urls represents the files at the local folder where SHP or GPKG were saved

    :returns
    -to_grid_code <Integer>
    YKR ID which represents where the Travel Times are based on the file
    '''

    # get the basename of the file to map
    data_path_basename = os.path.basename(ykr_file_path)

    # conditional for getting the YKR code for gpkg and shp
    if data_path_basename[-1] == 'g':
        to_grid_code = int(data_path_basename[-12:-5])

    elif data_path_basename[-1] == 'p':
        to_grid_code = int(data_path_basename[-11:-4])

    return to_grid_code


def to_ykr_grid(ykr_file_path):
    '''
    Def which gives back the YKR grid <GeoDataFrame> where the accessibility is measured
    ------------------------------------------------------------------------------------

    :param
    - ykr_file_path <url of SHP or GPKG>
    this urls represents the files at the local folder where SHP or GPKG were saved

    :return
    - grid_sub <GeoDataFrame>
    grid_sub contains one element which is the grid where accessibility is measured
    '''

    # getting the YKR ID with URL with function
    to_grid_code = ykr_grid_code(ykr_file_path)

    # reading the entire YKR Grid
    grid_sub = read_grid(grid_path)

    # subset of grid based of the code of the file
    grid_sub = grid_sub.loc[grid_sub['YKR_ID'] == to_grid_code]

    return grid_sub


def get_map_list():
    '''
    Def which gives back a list with the local urls of the downloaded layers
    ------------------------------------------------------------------------
    - If SHP or GPKG is repeated, this Def avoid duplicate urls in the list
    - Also avoid other SHP or GPKG downloaded

    :returns
    - list_to_map <list> with URLS in local folder to map
    '''

    # getting the local folder url from button
    local_folder = user_url.value

    # kind of downloads to be evaluated
    layers = ['shp', 'gpkg']

    # list with all the layers in local folder. List of lists
    map_list = []

    # iteration with SHP and GPKG to get all urls
    for layer in layers:
        map_list_loop = glob.glob(r'{}/travel_times*{}'.format(local_folder, layer))

        map_list.append(map_list_loop)

    # subset of list giving back: list of shp urls, and list of gpkg urls
    shp_list = map_list[0]
    gpkg_list = map_list[1]

    # one list with all layers urls
    layers_list = shp_list + gpkg_list

    # obtaining the YKR codes of shp urls and gpkg urls
    layer_codes_shp = list(set([layer_code[-11:-4] for layer_code in shp_list]))
    layer_codes_gpkg = list(set([layer_code[-12:-5] for layer_code in gpkg_list]))

    # list with unique YKR codes of shp and gpkg
    layer_unique_codes = list(set(layer_codes_shp + layer_codes_gpkg))

    # list with unique urls
    list_to_map = []
    list_to_test = []

    # iteration to erase exceptions like comparison layers
    for exceptions in layers_list:
        if 'comp' not in os.path.basename(exceptions):
            list_to_test.append(exceptions)

    # iteration to avoid duplicates
    for layer_code in layer_unique_codes:
        for layer_url in list_to_test:
            if layer_code in layer_url:
                list_to_map.append(layer_url)
                break

    return list_to_map

def name_of_mode(all_modes, function_botton):
    '''
    Def which gives back the name of the Transport Mode to be mapped, based ond the user selection
    ----------------------------------------------------------------------------------------------
    :param
    - all_modes <list of tuples>
    all_modes is defined in the notebook with the name of the Transport Mode which is shown in the
    dropdown menu

    - function_button <Function>
    this function should give back the selected Transport Mode for the user. The one specified at the
    dropdown menu widget

    :return
    - name_mode <str> name of the selected Transport Mode to be used in the map layout
    '''
    # iterating over all modes
    for file in all_modes:
        if function_botton == file[1]:

            # name which is going to be used at the maps
            name_mode = file[0]
    return name_mode

def selected_t_mode(t_mode_button):
    '''
    Def which gives back the selected Transport Mode at the Dropdown menu Widget
    ----------------------------------------------------------------------------
    :param
    - t_mode_button <Widget>

    :return
    - t_mode_button.value <str> selected from dropdown menu
    '''
    return t_mode_button.value

def selected_scheme(class_button):
    '''
    Def which gives back the selected Classification Scheme
    -------------------------------------------------------
    :param
    - class_button <Widget>

    :return
    - class_button.value <str> selected from dropdown menu
    '''
    return class_button.value

def selected_cmap(color_button):
    '''
    Def which gives back the selected Color Map
    -------------------------------------------------------
    :param
    - color_button <Widget>

    :return
    - color_button.value <str> selected from dropdown menu
    '''
    return color_button.value

def selected_alpha(alpha_button):
    '''
    Def which gives back the selected Transparency of the layer
    -------------------------------------------------------
    :param
    - alpha_button <Widget>

    :return
    - alpha_button.value <str> selected from dropdown menu
    '''
    return alpha_button.value

def selected_nclasses(classes_button):
    '''
    Def which gives back the selected Number of Classes
    -------------------------------------------------------
    :param
    - classes_button <Widget>

    :return
    - classes_button.value <str> selected from dropdown menu
    '''
    return classes_button.value


def map_selected_files(map_button):
    '''
    Def which gives back the Files at Local Folder (downloaded SHP or GPKG) as a MAP with the selected parameters
    -------------------------------------------------------------------------------------------------------------
    :param
    - map_button <Widget button>

    :return
    - MAPS IN DISPLAY (visualization)
    '''
    plt.style.use('seaborn-dark')

    # list of files in the local folder
    files_list = get_map_list()

    # enumerating the files ot be mapped
    n_maps = [n for n in range(len(files_list))]

    with map_out:
        clear_output()

    # iterates over files to map
    for map_file, n in zip(files_list, n_maps):
        with map_out:
            # clear_output()
            print('Mapping... {}/{}'.format(n + 1, len(files_list)))

        # reading the data and projecting to Mercator (because of basemap)
        data = gpd.read_file(map_file)
        data = data.to_crs(3857)

        # reading and projecting the grid but only the cell the travel times are based
        to_ykr_grid_cell = to_ykr_grid(map_file)
        to_ykr_grid_cell = to_ykr_grid_cell.to_crs(3857)

        # reading and projecting the sea
        sea_map = read_sea()
        sea_map = sea_map.to_crs(3857)

        # PLOTTING

        # create base ax
        fig, ax = plt.subplots(figsize=[13, 9])

        # plot map data
        data.plot(ax=ax, column=selected_t_mode(t_mode_button),
                  scheme=selected_scheme(class_button),
                  k=selected_nclasses(classes_button),
                  cmap=selected_cmap(color_button),
                  alpha=selected_alpha(alpha_button),
                  legend_kwds={"fmt": "{:.0f}"},
                  edgecolor='None',
                  linewidth=0,
                  legend=True)

        # plot cell to analyze
        to_ykr_grid_cell.plot(ax=ax, facecolor='red', edgecolor='black', linewidth=0.4)

        # plot sea
        sea_map.plot(ax=ax, facecolor='#00006c')

        # limits in Mercator
        ax.set_xlim(2720000, 2820000)
        ax.set_ylim(8420000, 8493000)

        # limits in WGS84
        # ax.set_xlim(24.46, 25.28)
        # ax.set_ylim(60.095, 60.41)

        # Turn off tick labels
        ax.set_yticklabels([]);
        ax.set_xticklabels([]);

        # legend anchor
        ax.get_legend().set_bbox_to_anchor((1.13, 1))

        # NAMES

        # title
        ax.title.set_text('Helsinki Travel Times by {} in YKR Grid {}' \
                          .format(name_of_mode(all_modes, selected_t_mode(t_mode_button)),
                                  ykr_grid_code(map_file)))

        # legend title
        ax.get_legend().set_title('minutes / class')

        # adding basemap
        ctx.add_basemap(ax, source=ctx.providers.Esri.WorldGrayCanvas,
                        attribution='AccessViz Mapper.\nUniversity of Helsinki.\nDigital Geography Lab')

        # display
        with map_out:
            plt.show()


def maps_as_png(save_png_button):
    '''
    Def which saves the visualized maps as PNG at the local downloads folder
    ------------------------------------------------------------------------
    :param
    - save_png_button <Widget Button>

    :return
    - Save automatic the Map files as PNG in the local downloads folder
    '''
    plt.style.use('seaborn-dark')

    # list of files in the local folder
    files_list = get_map_list()

    # enumerating the files
    n_maps = [n for n in range(len(files_list))]

    with map_out:
        clear_output()

    # iterates over files to map
    for map_file, n in zip(files_list, n_maps):
        with map_out:
            print('Saving Map as PNG... {}/{}'.format(n + 1, len(files_list)))

        # reading the data and projecting to Mercator (because of basemap)
        data = gpd.read_file(map_file)
        data = data.to_crs(3857)

        # reading and projecting the grid but only the cell the travel times are based
        to_ykr_grid_cell = to_ykr_grid(map_file)
        to_ykr_grid_cell = to_ykr_grid_cell.to_crs(3857)

        # reading and projecting the sea
        sea_map = read_sea()
        sea_map = sea_map.to_crs(3857)

        # PLOTTING

        # create base ax
        fig, ax = plt.subplots(figsize=[13, 9])

        # plot map data
        data.plot(ax=ax, column=selected_t_mode(t_mode_button),
                  scheme=selected_scheme(class_button),
                  k=selected_nclasses(classes_button),
                  cmap=selected_cmap(color_button),
                  alpha=selected_alpha(alpha_button),
                  legend_kwds={"fmt": "{:.0f}"},
                  edgecolor='None',
                  linewidth=0,
                  legend=True)

        # plot cell to analyze
        to_ykr_grid_cell.plot(ax=ax, facecolor='red', edgecolor='black', linewidth=0.4)

        # plot sea
        sea_map.plot(ax=ax, facecolor='#00006c')

        # limits in Mercator
        ax.set_xlim(2720000, 2820000)
        ax.set_ylim(8420000, 8493000)

        # limits in WGS84
        # ax.set_xlim(24.46, 25.28)
        # ax.set_ylim(60.095, 60.41)

        # Turn off tick labels
        ax.set_yticklabels([]);
        ax.set_xticklabels([]);

        # legend
        ax.get_legend().set_bbox_to_anchor((1.13, 1))

        # NAMES

        # title
        ax.title.set_text('Helsinki Travel Times by {} in YKR Grid {}' \
                          .format(name_of_mode(all_modes, selected_t_mode(t_mode_button)),
                                  ykr_grid_code(map_file)))

        # legend title
        ax.get_legend().set_title('minutes / class')

        # add basemap
        ctx.add_basemap(ax, source=ctx.providers.Esri.WorldGrayCanvas,
                        attribution='AccessViz Mapper.\nUniversity of Helsinki.\nDigital Geography Lab')

        # define a name of png file
        name_map = os.path.join(user_url.value, 'Accessibility_{}_YKRID_{}.png' \
                                .format(name_of_mode(all_modes, selected_t_mode(t_mode_button)),
                                        ykr_grid_code(map_file)))

        # saving...
        plt.savefig(name_map, dpi=300)

        with map_out:
            print('Map saved in: {}\n'.format(name_map))

In [53]:
# tuples with Transportation Modes and given names
t_modes = [('Walking','walk_t'), 
           ('Bike Slow Speed', 'bike_s_t'),
           ('Bike Fast Speed','bike_f_t'),
           ('Public Transport Rush Hour Whole Chain', 'pt_r_tt'),
           ('Public Transport Rush Hour','pt_r_t'),
           ('Public Transport Midday Traffic Whole Chain','pt_m_tt'),
           ('Public Transport Midday Traffic','pt_m_t'),
           ('Car Rush Hour Whole Chain','car_r_t'),
           ('Car Midday Whole Chain','car_m_t'),
           ('Car with Speed Limit','car_sl_t')]

all_modes = [('Walking','walk_t'),
            ('Bike Slow Speed', 'bike_s_t'),
            ('Bike Fast Speed','bike_f_t'),
             ('Public Transport Rush Hour Whole Chain', 'pt_r_tt'),
             ('Public Transport Rush Hour','pt_r_t'),
             ('Public Transport Midday Traffic Whole Chain','pt_m_tt'),
             ('Public Transport Midday Traffic','pt_m_t'),
             ('Car Rush Hour Whole Chain','car_r_t'),
             ('Car Midday Whole Chain','car_m_t'),
             ('Car with Speed Limit','car_sl_t'),
             ('Walking Distance','walk_d'),
             ('Bike Distance','bike_d'),
             ('Public Transport Rush Hour Distance', 'pt_r_d'),
             ('Public Transport Midday Distance','pt_m_d'),
             ('Car Rush Hour Distance','car_r_d'),
             ('Car Midday Distance','car_m_d')]

class_scheme = [('Equal Intervals','equalinterval'),
                ('Natural Breaks', 'naturalbreaks'), 
                ('Quantiles','quantiles')]

color_map = [('Viridis    #Sequential change','viridis'), 
             ('Yellow - Green - Blue    #Sequential change','YlGnBu'),
             ('Turquese - Purple    #Sequential change', 'cool'),
             ('Pink - Green    #Diverging change', 'PiYG'),
             ('Red - Yellow - Blue    #Diverging change', 'RdYlBu'),
             ('Red - Yellow - Gren    #Diverging change', 'RdYlGn'),
             ('Red - Blue    #Diverging change', 'RdBu')]
            
#----------------------------------------------------------------------------------------------------

# adding a button widget to map downloaded files. Tooltip is an action which run after click on the button.
map_button = widgets.Button(description='Map files', 
                            disabled=False, 
                            button_style='success', 
                            tooltip='Click me', 
                            icon='map')

# adding the combobox widget. Combobox means that you can type and select the correct one.
t_mode_button = widgets.Dropdown(placeholder='Select transport mode', 
                                 options=t_modes, description='Mode:',
                                 value = 'pt_r_t',
                                 ensure_option=True, 
                                 disabled=False)

class_button = widgets.Dropdown(placeholder='Select classification scheme', 
                                 options=class_scheme, description='Scheme:',
                                 value = 'naturalbreaks',
                                 ensure_option=True, 
                                 disabled=False)

color_button = widgets.Dropdown(placeholder='Select a color map', 
                                 options = color_map, description='Cmap:',
                                 value = 'PiYG',
                                 ensure_option=True, 
                                 disabled=False)

alpha_button = widgets.FloatSlider(value=0.9,
                                   min=0,
                                   max=1,
                                   step=0.1,
                                   description='Alpha:',
                                   disabled=False,
                                   continuous_update=False,
                                   orientation='horizontal',
                                   readout=True,
                                   readout_format='.1f')

classes_button = widgets.IntSlider(value=11,
                                   min=2,
                                   max=20,
                                   step=1,
                                   description='N Classes:',
                                   disabled=False,
                                   continuous_update=False,
                                   orientation='horizontal',
                                   readout=True,
                                   readout_format='d')

save_png_button = widgets.Button(description='Save maps PNG', 
                            disabled=False, 
                            button_style='primary', 
                            tooltip='Click me', 
                            icon='download')

# ------------------------------------------------------------------------------------

# output variable is used to display in rendering the map
map_out = widgets.Output()

# adding the click event to the button. To add event you do it as a function
map_button.on_click(map_selected_files)
save_png_button.on_click(maps_as_png)

# ------ TO DISPLAY -------

display(t_mode_button)
display(class_button)
display(color_button)
display(alpha_button)
display(classes_button)

display(map_button)
display(save_png_button)

display(map_out)

Dropdown(description='Mode:', index=4, options=(('Walking', 'walk_t'), ('Bike Slow Speed', 'bike_s_t'), ('Bike…

Dropdown(description='Scheme:', index=1, options=(('Equal Intervals', 'equalinterval'), ('Natural Breaks', 'na…

Dropdown(description='Cmap:', index=3, options=(('Viridis    #Sequential change', 'viridis'), ('Yellow - Green…

FloatSlider(value=0.9, continuous_update=False, description='Alpha:', max=1.0, readout_format='.1f')

IntSlider(value=11, continuous_update=False, description='N Classes:', max=20, min=2)

Button(button_style='success', description='Map files', icon='map', style=ButtonStyle(), tooltip='Click me')

Button(button_style='primary', description='Save maps PNG', icon='download', style=ButtonStyle(), tooltip='Cli…

Output()

## ***4. Comparing Travel Times and Distances - Tool***
________________________
Select the Transport Modes you want to compare. Then, visualize/download the Map Comparison of Travel Times.

In [54]:
# -----------------------------------------------------------------------------
#                                   FUNCTIONS
# -----------------------------------------------------------------------------

def selected_st_mode(st_mode_button):
    '''
    Def which gives back the selected First Transport Mode for Comparison
    -----------------------------------------------------------
    :param
    - st_mode_button <Widget button>

    :return
    - st_mode_button.value <str>
    first selected transportation mode
    '''
    return st_mode_button.value

def selected_nd_mode(nd_mode_button):
    '''
    Def which gives back the selected Second Transport Mode for Comparison
    -----------------------------------------------------------
    :param
    - nd_mode_button <Widget button>

    :return
    - nd_mode_button.value <str>
    first selectede transportation mode
    '''
    return nd_mode_button.value


def comparison_modes_list():
    '''
    Def which gives back the pair of Transport Modes
    ------------------------------------------------
    The condition is that it evaluates that only can be paired Time - Time, or Distance - Distance

    :return
    - selected_modes <list> with two correct selected Transport Modes
    '''

    # define first and second selected mode
    st = selected_st_mode(st_mode_button)
    nd = selected_nd_mode(nd_mode_button)

    selected_modes = []

    # conditional to select pairs. Time with time, and distance with distance
    if st[-1] == nd[-1]:

        # appending if they pair up
        selected_modes.append(st)
        selected_modes.append(nd)

        with comp_out:
            clear_output()
            print('Transportation Modes selected are correct!')
    else:
        with comp_out:
            clear_output()
            print('You only can compare Time-Time or Distance-Distance =D')

    return selected_modes


def map_comparison_modes(map_comp_button):
    '''
    Def which gives back map visualization of the selected transport modes to compare Travel Times
    ----------------------------------------------------------------------------------------------

    :param
    - map_comp_button <Widget Button> for on click event

    :return
    - map visualization in display
    '''

    with comp_out:
        clear_output()

    # call the list with the selected modes
    selected_modes = comparison_modes_list()

    # conditional that must be selected at least 2 modes
    if len(selected_modes) != 0:
        plt.style.use('seaborn-dark')

        # list of files in the local folder
        files_list = get_map_list()

        # number of maps to plot
        n_maps = [n for n in range(len(files_list))]

        # iterates over files to map
        for map_file, n in zip(files_list, n_maps):

            with comp_out:
                # clear_output()
                print('Mapping comparison... {}/{}'.format(n + 1, len(files_list)))

            # reading the data and projecting to Mercator (because of basemap)
            data = gpd.read_file(map_file)
            data = data.to_crs(3857)

            # selecting codes for naming column
            st_code = selected_modes[0].split('_')
            nd_code = selected_modes[1].split('_')

            # creating a new column for calculate comparison
            column_name = '{}_vs_{}'.format(st_code[0], nd_code[0])

            data[column_name] = data[selected_modes[0]] - data[selected_modes[1]]

            # reading and projecting the grid but only the cell the travel times are based
            to_ykr_grid_cell = to_ykr_grid(map_file)
            to_ykr_grid_cell = to_ykr_grid_cell.to_crs(3857)

            # reading and projecting the sea
            sea_map = read_sea()
            sea_map = sea_map.to_crs(3857)

            # PLOTTING

            # create base ax
            fig, ax = plt.subplots(figsize=[13, 9])

            # plot map data
            data.plot(ax=ax, column=column_name,
                      scheme=selected_scheme(class_button),
                      k=selected_nclasses(classes_button),
                      cmap=selected_cmap(color_button),
                      legend_kwds={"fmt": "{:.0f}"},
                      alpha=selected_alpha(alpha_button),
                      edgecolor='None',
                      linewidth=0,
                      legend=True)

            # plot cell to analyze
            to_ykr_grid_cell.plot(ax=ax, facecolor='red', edgecolor='black', linewidth=0.4)

            # plot sea
            sea_map.plot(ax=ax, facecolor='#00006c')

            # limits in Mercator
            ax.set_xlim(2720000, 2820000)
            ax.set_ylim(8420000, 8493000)

            # limits in WGS84
            # ax.set_xlim(24.46, 25.28)
            # ax.set_ylim(60.095, 60.41)

            # Turn off tick labels
            ax.set_yticklabels([]);
            ax.set_xticklabels([]);

            # NAMES

            if st_code[-1] == 't' or nd_code[-1]:
                comp_name = 'Times'
            else:
                comp_name = 'Distances'

                # title
            ax.title.set_text('Helsinki Travel {} Comparison *{} vs {}* in YKR Grid {}' \
                              .format(comp_name,
                                      name_of_mode(all_modes, selected_st_mode(st_mode_button)),
                                      name_of_mode(all_modes, selected_nd_mode(nd_mode_button)),
                                      ykr_grid_code(map_file)))

            # legend title
            ax.get_legend().set_title('{} {} - {} {}'.format(st_code[0], comp_name[0], nd_code[0], comp_name[0]))

            ax.get_legend().set_bbox_to_anchor((1.13, 1))

            ctx.add_basemap(ax, source=ctx.providers.Esri.WorldGrayCanvas,
                            attribution='AccessViz Mapper.\nUniversity of Helsinki.\nDigital Geography Lab')

            with comp_out:
                plt.show()


def maps_comp_as_png(save_png_comp_button):
    '''
    Def which saves the comparison maps as PNG
    ------------------------------------------
    :param
    - save_png_com_button <Widget button> with click on event

    :return
    - Automatic it saves PNG files of the visualized maps
    '''

    with comp_out:
        clear_output()

    # call the list with the selected modes
    selected_modes = comparison_modes_list()

    if len(selected_modes) != 0:
        plt.style.use('seaborn-dark')

        # list of files in the local folder
        files_list = get_map_list()

        # number of maps to plot
        n_maps = [n for n in range(len(files_list))]

        # iterates over files to map
        for map_file, n in zip(files_list, n_maps):

            with comp_out:
                # clear_output()
                print('Saving comparison map... {}/{}'.format(n + 1, len(files_list)))

            # reading the data and projecting to Mercator (because of basemap)
            data = gpd.read_file(map_file)
            data = data.to_crs(3857)

            # selecting codes for naming column
            st_code = selected_modes[0].split('_')
            nd_code = selected_modes[1].split('_')

            # creating a new column for calculate comparison
            column_name = '{}_vs_{}'.format(st_code[0], nd_code[0])

            data[column_name] = data[selected_modes[0]] - data[selected_modes[1]]

            # reading and projecting the grid but only the cell the travel times are based
            to_ykr_grid_cell = to_ykr_grid(map_file)
            to_ykr_grid_cell = to_ykr_grid_cell.to_crs(3857)

            # reading and projecting the sea
            sea_map = read_sea()
            sea_map = sea_map.to_crs(3857)

            # PLOTTING

            # create base ax
            fig, ax = plt.subplots(figsize=[13, 9])

            # plot map data
            data.plot(ax=ax, column=column_name,
                      scheme=selected_scheme(class_button),
                      k=selected_nclasses(classes_button),
                      cmap=selected_cmap(color_button),
                      legend_kwds={"fmt": "{:.0f}"},
                      alpha=selected_alpha(alpha_button),
                      edgecolor='None',
                      linewidth=0,
                      legend=True)

            # plot cell to analyze
            to_ykr_grid_cell.plot(ax=ax, facecolor='red', edgecolor='black', linewidth=0.4)

            # plot sea
            sea_map.plot(ax=ax, facecolor='#00006c')

            # limits in Mercator
            ax.set_xlim(2720000, 2820000)
            ax.set_ylim(8420000, 8493000)

            # limits in WGS84
            # ax.set_xlim(24.46, 25.28)
            # ax.set_ylim(60.095, 60.41)

            # Turn off tick labels
            ax.set_yticklabels([]);
            ax.set_xticklabels([]);

            # NAMES

            # conditional to name it in map *title
            if st_code[-1] == 't' or nd_code[-1]:
                comp_name = 'Times'
            else:
                comp_name = 'Distances'

            # title
            ax.title.set_text('Helsinki Travel {} Comparison *{} vs {}* in YKR Grid {}' \
                              .format(comp_name,
                                      name_of_mode(all_modes, selected_st_mode(st_mode_button)),
                                      name_of_mode(all_modes, selected_nd_mode(nd_mode_button)),
                                      ykr_grid_code(map_file)))

            # legend title
            ax.get_legend().set_title('{} {} - {} {}'.format(st_code[0], comp_name[0], nd_code[0], comp_name[0]))

            ax.get_legend().set_bbox_to_anchor((1.13, 1))

            ctx.add_basemap(ax, source=ctx.providers.Esri.WorldGrayCanvas,
                            attribution='AccessViz Mapper.\nUniversity of Helsinki.\nDigital Geography Lab')

            # name comparison map
            name_comp_map = os.path.join(user_url.value, 'Accessibility_YKRID_{}_{}_vs_{}.png' \
                                         .format(ykr_grid_code(map_file),
                                                 name_of_mode(all_modes, selected_st_mode(st_mode_button)),
                                                 name_of_mode(all_modes, selected_st_mode(nd_mode_button))))

            # saving map
            plt.savefig(name_comp_map, dpi=300)

            with comp_out:
                print('Map saved in: {}\n'.format(name_comp_map))
                # plt.show()


def save_compmap_shp(shp_comp_button):
    '''
    Def which saves YKR ID with travel time info + comparison column as SHP
    -----------------------------------------------------------------------
    :param
    - shp_comp_button <Widget button>
    :return
    - Automatic saves SHP files of the comparison Travel Times
    '''

    with comp_out:
        clear_output()

    # call the list with the selected modes
    selected_modes = comparison_modes_list()

    if len(selected_modes) != 0:
        # plt.style.use('seaborn-dark')

        # list of files in the local folder
        files_list = get_map_list()

        # number of maps to plot
        n_maps = [n for n in range(len(files_list))]

        # iterates over files to map
        for map_file, n in zip(files_list, n_maps):

            with comp_out:
                # clear_output()
                print('Saving comparison map SHP... {}/{}'.format(n + 1, len(files_list)))

            # reading the data and projecting to Mercator (because of basemap)
            data = gpd.read_file(map_file)
            data = data.to_crs(3857)

            # selecting codes for naming column
            st_code = selected_modes[0].split('_')
            nd_code = selected_modes[1].split('_')

            # creating a new column for calculate comparison
            column_name = '{}_vs_{}'.format(st_code[0], nd_code[0])

            data[column_name] = data[selected_modes[0]] - data[selected_modes[1]]

            # NAMES

            if st_code[-1] == 't' or nd_code[-1]:
                comp_name = 'Times'
            else:
                comp_name = 'Distances'

            # name comparison map
            name_comp_shp = os.path.join(user_url.value, 'travel_{}_comp_to_{}_{}_vs_{}.shp' \
                                         .format(comp_name,
                                                 ykr_grid_code(map_file),
                                                 st_code[0],
                                                 nd_code[0]))

            # saving file
            data.to_file(name_comp_shp)

            with comp_out:
                print('SHP saved in: {}\n'.format(name_comp_shp))


def save_compmap_gpkg(gpkg_comp_button):
    '''
    Def which saves YKR ID with travel time info + comparison column as SHP
    -----------------------------------------------------------------------
    :param
    - gpkg_comp_button <Widget button>
    :return
    - Automatic saves SHP files of the comparison Travel Times
    -
    '''

    with comp_out:
        clear_output()

    # call the list with the selected modes
    selected_modes = comparison_modes_list()

    if len(selected_modes) != 0:

        # list of files in the local folder
        files_list = get_map_list()

        # number of maps to plot
        n_maps = [n for n in range(len(files_list))]

        # iterates over files to map
        for map_file, n in zip(files_list, n_maps):

            with comp_out:
                # clear_output()
                print('Saving comparison map GPKG... {}/{}'.format(n + 1, len(files_list)))

            # reading the data and projecting to Mercator (because of basemap)
            data = gpd.read_file(map_file)
            data = data.to_crs(3857)

            # selecting codes for naming column
            st_code = selected_modes[0].split('_')
            nd_code = selected_modes[1].split('_')

            # creating a new column for calculate comparison
            column_name = '{}_vs_{}'.format(st_code[0], nd_code[0])

            data[column_name] = data[selected_modes[0]] - data[selected_modes[1]]

            # NAMES

            # conditional to write the name in title
            if st_code[-1] == 't' or nd_code[-1]:
                comp_name = 'Times'
            else:
                comp_name = 'Distances'

            # name comparison map
            name_comp_gpkg = os.path.join(user_url.value, 'travel_{}_comp_to_{}_{}_vs_{}.gpkg' \
                                          .format(comp_name,
                                                  ykr_grid_code(map_file),
                                                  st_code[0],
                                                  nd_code[0]))

            # saving file
            data.to_file(name_comp_gpkg, driver='GPKG')

            with comp_out:
                print('GPKG saved in: {}\n'.format(name_comp_gpkg))

In [55]:
               
# ------------------------------------------------------------------------------------------------
                                                                                      
# adding widgets of Comparison Travel Times
st_mode_button = widgets.Dropdown(placeholder='Select first transport mode', 
                                 options=all_modes, description='1st Mode:',
                                 value = 'bike_s_t',
                                 ensure_option=True, 
                                 disabled=False)

nd_mode_button = widgets.Dropdown(placeholder='Select second transport mode', 
                                 options=all_modes, description='2nd Mode:',
                                 value = 'car_r_t',
                                 ensure_option=True, 
                                 disabled=False)

map_comp_button = widgets.Button(description='Map comparison', 
                                 disabled=False, 
                                 button_style='success', 
                                 tooltip='Click me', 
                                 icon='map')

save_png_comp_button = widgets.Button(description='Save maps PNG',
                                      disabled=False, 
                                      button_style='primary', 
                                      tooltip='Click me', 
                                      icon='download')

shp_comp_button = widgets.Button(description='Save as SHP',
                                 disabled=False,
                                 button_style='primary',
                                 tooltip='Click me', 
                                 icon='download')

gpkg_comp_button = widgets.Button(description='Save as GPKG', 
                                  disabled=False, 
                                  button_style='primary',
                                  tooltip='Click me', 
                                  icon='download')

# ----------------------------------------------------------------------------------------

comp_out = widgets.Output()
                                           
# adding the click event to the button. To add event you do it as a function
map_comp_button.on_click(map_comparison_modes)
save_png_comp_button.on_click(maps_comp_as_png)

shp_comp_button.on_click(save_compmap_shp)
gpkg_comp_button.on_click(save_compmap_gpkg)
                                           
# ------------------------
# TO DISPLAY


display(st_mode_button)
display(nd_mode_button)

display(class_button)
display(color_button)
display(alpha_button)
display(classes_button)


display(map_comp_button)
display(save_png_comp_button)
display(shp_comp_button)
display(gpkg_comp_button)

display(comp_out)

Dropdown(description='1st Mode:', index=1, options=(('Walking', 'walk_t'), ('Bike Slow Speed', 'bike_s_t'), ('…

Dropdown(description='2nd Mode:', index=7, options=(('Walking', 'walk_t'), ('Bike Slow Speed', 'bike_s_t'), ('…

Dropdown(description='Scheme:', index=1, options=(('Equal Intervals', 'equalinterval'), ('Natural Breaks', 'na…

Dropdown(description='Cmap:', index=3, options=(('Viridis    #Sequential change', 'viridis'), ('Yellow - Green…

FloatSlider(value=0.9, continuous_update=False, description='Alpha:', max=1.0, readout_format='.1f')

...

Button(button_style='success', description='Map comparison', icon='map', style=ButtonStyle(), tooltip='Click m…

Button(button_style='primary', description='Save maps PNG', icon='download', style=ButtonStyle(), tooltip='Cli…

Button(button_style='primary', description='Save as SHP', icon='download', style=ButtonStyle(), tooltip='Click…

Button(button_style='primary', description='Save as GPKG', icon='download', style=ButtonStyle(), tooltip='Clic…

Output()

## ***5. Shortest Path - Routing Tool***
________________________
Select the YKR IDs you want to find the Shortest Path(s). You can include few Origins and Destinations. Then, choose the Network Type, Color Map of Shortest Paths(s). Finally, visualize/download the map of Shortest Path(s). Try some YKR IDs in the sample fata like: *Origins:* `5963655`. *Destinations:* `5925860`, `5933038`, `5816105`. 

In [56]:
import osmnx as ox
import networkx as nx
from shapely.geometry import Point, Polygon, LineString

In [57]:
# -----------------------------------------------------------------------------
#                                   FUNCTIONS
# -----------------------------------------------------------------------------
def path_origin_button_clicked(add_id_origin):
    '''
    Def used to append and print in display the selected YKR IDs origin for shortest path
    -------------------------------------------------------------------------------
    :param
    - add_id_origin <Widget Button>
    :return
    - display the selected YKR ID for origin of shortest path
    '''

    # conditional to avoid repeated origins and/or destinations
    if select_origin_id.value not in origin_ids and select_origin_id.value not in destin_ids:
        if select_origin_id.value != '':
            origin_ids.append(select_origin_id.value)

            with o_out:
                return print('Origin(s) YKR IDs: {}'.format(origin_ids))


def path_destin_button_clicked(add_id_destin):
    '''
    Def used to append and print in display the selected YKR IDs destination for shortest path
    -------------------------------------------------------------------------------
    :param
    - add_id_destin <Widget Button>
    :return
    - display the selected YKR ID for origin of shortest path
    '''

    # conditional to avoid repeated origins and/or destinations
    if select_destin_id.value not in destin_ids and select_destin_id.value not in origin_ids:
        if select_destin_id.value != '':
            destin_ids.append(select_destin_id.value)

            with d_out:
                return print('Destination(s) YKR IDs: {}'.format(destin_ids))


def origin_button_clear(clear_origin_ids):
    '''
    Def used to clear selected YKR IDs
    ----------------------------------
    :param
    - clear_origin_ids <Widget button>
    :return
    - Clear list with selected origins YKR IDs
    '''

    origin_ids.clear()

    with o_out:
        clear_output()
        return print('Origin(s) YKR IDs cleared!: {}\n'.format(origin_ids))


def destin_button_clear(clear_destin_ids):
    '''
    Def used to clear selected YKR IDs
    ----------------------------------
    :param
    - clear_destin_ids <Widget button>
    :return
    - Clear list with selected destinations YKR IDs
    '''

    destin_ids.clear()

    with d_out:
        clear_output()
        return print('Destination(s) YKR IDs cleared!: {}\n'.format(destin_ids))

# ------------------------- NETWORK TYPE SELECTION ---------------------------------------

def selected_path_cmap(color_path_button):
    '''
    Def which gives back the selected Color Map
    -------------------------------------------
    :param
    color_path_button <Widget Button>
    :return
    color_path_button.value <str> Color map of Routes
    '''
    return color_path_button.value

def selected_network_type():
    '''
    Def which gives back the value selected at the Network Type
    ----------------------------------------------------------
    '''
    return select_network_button.value


def OD_list(origin_ids, destin_ids):
    '''
    Def which gives back the YKR Grid centroids with the selected YKR IDs origins and destinations
    ----------------------------------------------------------------------------------------------
    :param
    - origin_ids <list> with selected origins YKR IDs
    - destin_ids <list> with selected destinations YKR IDs
    :return
    - [origin_centroids, destin_centroids] <list> list with 2 elements <lists>.
    first list is centroids of origins, second list is centroids of destinations
    '''

    # creating empty lists
    origin_centroids = []
    destin_centroids = []

    for origin_id in origin_ids:
        # reading the entire YKR Grid
        grid_path_sub = read_grid(grid_path)
        grid_path_sub['YKR_ID'] = grid_path_sub['YKR_ID'].astype(str)

        # subset of grid based of the code of the file
        grid_path_sub = grid_path_sub.loc[grid_path_sub['YKR_ID'] == origin_id]

        # projecting to local epsg to measure distances
        # grid_path_sub = grid_path_sub[['geometry']].to_crs(epsg = 32635)

        # define index for locating geometry
        geom_index = grid_path_sub.index[0]

        # centroid
        centroid_geom = grid_path_sub.at[geom_index, 'geometry'].centroid

        # List of Origins:
        centroidxy = (centroid_geom.x, centroid_geom.y)

        # appending to a list
        origin_centroids.append(centroidxy)

    for destin_id in destin_ids:
        # reading the entire YKR Grid
        grid_path_sub = read_grid(grid_path)
        grid_path_sub['YKR_ID'] = grid_path_sub['YKR_ID'].astype(str)

        # subset of grid based of the code of the file
        grid_path_sub = grid_path_sub.loc[grid_path_sub['YKR_ID'] == destin_id]

        # projecting to local epsg to measure distances
        # grid_path_sub = grid_path_sub[['geometry']].to_crs(epsg = 32635)

        # define index for locating geometry
        geom_index = grid_path_sub.index[0]

        # centroid
        centroid_geom = grid_path_sub.at[geom_index, 'geometry'].centroid

        # List of Origins
        centroidxy = (centroid_geom.x, centroid_geom.y)

        # appending to a list
        destin_centroids.append(centroidxy)

    return [origin_centroids, destin_centroids]


def graph_extent_bbox(origin_centroids_list, destin_centroids_list):
    '''
    Def which gives back the bounding box of the origins and destinations
    ---------------------------------------------------------------------
    :param
    - origin_centroids_list <list>
    - destin_centroids_list <list>

    :return
    graph_extent <Geometry Object Polygon>
    Extension of the Origins and Destinations
    '''

    # all points in list
    all_OD_coors = origin_centroids_list + destin_centroids_list

    # all points dataframe
    all_points = gpd.GeoDataFrame(columns=['geometry'], geometry='geometry', crs=CRS.from_epsg(4326))  # 32635
    all_points['geometry'] = [Point(pair_coors) for pair_coors in all_OD_coors]

    # defyning a bounding box
    total_bounds = all_points['geometry'].total_bounds

    xmin = total_bounds[0]
    ymin = total_bounds[1]
    xmax = total_bounds[2]
    ymax = total_bounds[3]

    bbox_coords = Polygon([[xmin, ymax], [xmin, ymin], [xmax, ymin], [xmax, ymax]])

    # adding buffer
    graph_extent = bbox_coords.buffer(0.02)

    return graph_extent


def fetch_graph_network(graph_extent):
    '''
    Def which gives back the Graph file with Network Selected and graph extent
    --------------------------------------------------------------------------

    '''

    # fetching graph
    graph = ox.graph_from_polygon(graph_extent, network_type=selected_network_type())

    # fig, ax = ox.plot_graph(graph)

    # reprojecting the graph
    graph_proj = ox.project_graph(graph)

    # obtaining geodataframes of nodes, edges
    nodes_proj, edges_proj = ox.graph_to_gdfs(graph_proj, nodes=True, edges=True)

    return graph


def find_shortest_path():
    '''
    Def which gives back a geodataframe(plot) with the Shortest Paths
    -----------------------------------------------------------------
    :return:
    - routes <GeoDataFrame> with shortest paths
    '''

    with path_out:
        print('Starting...')

    # getting the origins and destinations ids
    all_OD = OD_list(origin_ids, destin_ids)
    origins_OD = all_OD[0]
    destins_OD = all_OD[1]

    # getting the bounding box of the network
    graph_bbox = graph_extent_bbox(origins_OD, destins_OD)

    with path_out:
        print('Fetching Network...')

    # getting the graph network in wgs84
    graph = fetch_graph_network(graph_bbox)

    # reprojecting the graph
    graph_proj = ox.project_graph(graph)

    # obtaining geodataframes of nodes, edges

    global nodes_proj
    global edges_proj
    nodes_proj, edges_proj = ox.graph_to_gdfs(graph_proj, nodes=True, edges=True)

    # Origins create a geodataframe with coordinates and project to the local UTM Zone epsg 32635
    origins_wgs = gpd.GeoDataFrame(columns=['geometry'], geometry='geometry', crs=CRS.from_epsg(4326))
    origins_wgs['geometry'] = [Point(origin_pair) for origin_pair in origins_OD]

    global orig_proj
    orig_proj = origins_wgs.to_crs(epsg=32635)

    # Destins create a geodataframe with coordinates and project to the local UTM Zone epsg 32635
    destins_wgs = gpd.GeoDataFrame(columns=['geometry'], geometry='geometry', crs=CRS.from_epsg(4326))
    destins_wgs['geometry'] = [Point(destin_pair) for destin_pair in destins_OD]

    global dest_proj
    dest_proj = destins_wgs.to_crs(epsg=32635)

    # Store the shortest path routes as LineString geometries in a GeoDataFrame called routes:
    routes = None

    # creating a list of origins and destination switched x and y.
    originsyx = [(point.y, point.x) for point in orig_proj['geometry']]
    destinationsyx = [(point.y, point.x) for point in dest_proj['geometry']]

    with path_out:
        print('Finding nodes...')

    # finding the nearest nodes for origins and destinations, in a list
    orig_node_id = [ox.get_nearest_node(graph_proj, orig_points, method='euclidean') for orig_points in originsyx]
    dest_node_id = [ox.get_nearest_node(graph_proj, dest_points, method='euclidean') for dest_points in destinationsyx]

    # creating routes with impedance length of the route and saving it in geodataframe
    routes = gpd.GeoDataFrame(columns=['geometry'], geometry='geometry', crs=edges_proj.crs)

    # list of routes geometries and osm ids
    routes_geom = []
    routes_osmids = []

    with path_out:
        print('Finding Shortest(s) Path(s)...')

    # iterating over origins and destinations.
    for origin_node in orig_node_id:
        for dest_node in dest_node_id:
            # if origin is the same as destination then no routing
            if origin_node == dest_node:
                skip
            else:
                # create route as graph object
                route = nx.shortest_path(G=graph_proj, source=origin_node, target=dest_node, weight='length')

                # getting the attributes of the route with nodes_proj
                route_nodes = nodes_proj.loc[route]

                # getting the osmid of the route from nodes_proj
                routes_osmid = str(route_nodes.osmid.astype(str).to_list())

                # creating a linestring with geometries
                route_line = LineString(route_nodes.geometry.to_list())

                # appending the linestring to a list to then add it to a gdf
                routes_geom.append(route_line)

                # appending the osmid to a list to then add it to a gdf
                routes_osmids.append(routes_osmid)

    # adding the attributes (lists) to the Geodataframe
    routes['geometry'] = routes_geom
    routes['osmids'] = routes_osmids

    return routes


def map_shortest_path(map_path_button):
    '''
    Def which display maps of the Shortest Path
    -------------------------------------------
    :param
    - map_path_button <Widget Button>
    :return
    - Map of shortest path in Display
    '''

    with path_out:
        clear_output()

    # get the routes
    global routes
    routes = find_shortest_path()

    # creating a new column with distance
    routes['route_dist'] = routes.length

    # PLOTTING

    global fig, ax
    # create base ax
    fig, ax = plt.subplots(figsize=[13, 9])

    # projecting data to display with basemap

    # plot map data
    routes.plot(ax=ax, column='route_dist',
                # scheme = selected_scheme(class_button),
                # k = selected_nclasses(classes_button),
                cmap=selected_path_cmap(color_path_button),
                alpha=0.8,
                # legend_kwds = {"fmt": "{:.1f}"},
                linewidth=3,
                zorder=1,
                legend=True)

    # plotting nodes
    global orig_proj
    orig_proj.plot(ax=ax, facecolor='black', markersize=14, zorder=2)

    global dest_proj
    dest_proj.plot(ax=ax, facecolor='red', markersize=14, zorder=3)

    # global edges_proj
    edges_proj.plot(ax=ax, edgecolor='dimgray', linewidth=0.4,
                    alpha=0.8)

    # Turn off tick labels
    ax.set_yticklabels([]);
    ax.set_xticklabels([]);

    # NAMES

    # title
    ax.title.set_text('Shortest Path in {} (meters)\nOrigin(s) YKR IDs: {}\nDestination(s) YKR IDs: {}' \
                      .format(name_of_mode(network_type, selected_network_type()),
                              origin_ids,
                              destin_ids))
    # white background
    ax.set_facecolor('xkcd:white')

    # set label x as attribution
    ax.set_xlabel('AccessViz Mapper.\nUniversity of Helsinki.\nDigital Geography Lab')

    with path_out:
        plt.show()


def shp_shortest_path(shp_path_button):
    '''
    Def which display maps of the Shortest Path
    -------------------------------------------
    :param
    - shp_path_button <Widget button>
    :return
    Saves the Routes as SHP at the local folder
    '''

    with path_out:
        clear_output()

    # get the routes
    # routes = find_shortest_path()

    # creating a new column with distance
    routes['route_dist'] = routes.length

    # name routes
    name_route = os.path.join(user_url.value, 'Shortest_Paths_{}_{}_origins_{}_destinations.shp' \
                              .format(name_of_mode(network_type, selected_network_type()),
                                      len(origin_ids),
                                      len(destin_ids)))
    with path_out:
        print('Saving...')

    # saving file
    routes.to_file(name_route)

    with path_out:
        print('Shortest Path(s) saved in: {}\n'.format(name_route))


def png_shortest_path(png_path_button):
    '''
    Def which save maps of the Shortest Path
    ----------------------------------------
    :param
    - png_path_button <Widget button>
    :return
    Saves PNG files of shortest path map
    '''

    with path_out:
        clear_output()

    # get the routes
    global routes
    routes = find_shortest_path()

    # creating a new column with distance
    routes['route_dist'] = routes.length

    # PLOTTING

    # create base ax
    fig, ax = plt.subplots(figsize=[13, 9])

    # plot map data
    routes.plot(ax=ax, column='route_dist',
                # scheme = selected_scheme(class_button),
                # k = selected_nclasses(classes_button),
                cmap=selected_path_cmap(color_path_button),
                alpha=0.8,
                # legend_kwds = {"fmt": "{:.1f}"},
                linewidth=3,
                zorder=1,
                legend=True)

    # plotting nodes
    global orig_proj
    orig_proj.plot(ax=ax, facecolor='black', markersize=12, zorder=2)

    global dest_proj
    dest_proj.plot(ax=ax, facecolor='red', markersize=12, zorder=3)

    # global edges_proj
    edges_proj.plot(ax=ax, edgecolor='dimgray', linewidth=0.4,
                    alpha=0.8)

    # Turn off tick labels
    ax.set_yticklabels([]);
    ax.set_xticklabels([]);

    # NAMES

    # title
    ax.title.set_text('Shortest Path in {} (meters)\nOrigin(s) YKR IDs: {}\nDestination(s) YKR IDs: {}' \
                      .format(name_of_mode(network_type, selected_network_type()),
                              origin_ids,
                              destin_ids))
    # white background
    ax.set_facecolor('xkcd:white')

    # set label x as attribution
    ax.set_xlabel('AccessViz Mapper.\nUniversity of Helsinki.\nDigital Geography Lab')

    with path_out:
        clear_output()
        print('Saving...')

    # name of map
    name_map_route = os.path.join(user_url.value, 'Shortest_Paths_{}_{}_origins_{}_destinations.png' \
                                  .format(name_of_mode(network_type, selected_network_type()),
                                          len(origin_ids),
                                          len(destin_ids)))

    # saving map
    plt.savefig(name_map_route, dpi=300)

    with path_out:
        print('Map saved in: {}\n'.format(name_map_route))
        # plt.show()

In [58]:
# creating a list of YKR IDs for shortest path (global variable)
origin_ids = []
destin_ids = []

# -----------------------------------------------------------------------------------------

# adding the combobox widget. Combobox means that you can type and select the correct one.
select_origin_id = widgets.Combobox(placeholder='Type/select the YKR ID', 
                                 options=grid_list, description='OriginID',
                                 ensure_option=True, 
                                 disabled=False)

select_destin_id = widgets.Combobox(placeholder='Type/select the YKR ID', 
                                 options=grid_list, description='DestinationID',
                                 ensure_option=True, 
                                 disabled=False)

# adding the button widget. Click Me Tooltip is an action which run after clicking on the button.
add_id_origin = widgets.Button(description='Add OriginID', 
                   disabled=False, 
                   button_style='info', 
                   tooltip='Click me', 
                   icon='check')

add_id_destin = widgets.Button(description='Add DestinationID', 
                   disabled=False, 
                   button_style='info', 
                   tooltip='Click me', 
                   icon='check')

clear_origin_ids = widgets.Button(description='Clear Origin(s)', 
                   disabled=False, 
                   button_style='danger', 
                   tooltip='Click me', 
                   icon='remove')

clear_destin_ids = widgets.Button(description='Clear Destin(s)', 
                   disabled=False, 
                   button_style='danger', 
                   tooltip='Click me', 
                   icon='remove')

# -----------------------------------------------------------------------------------------

# output variable is used to display in rendering the selected variable
o_out = widgets.Output()
d_out = widgets.Output()
        
# adding the click event to the button. To add event you do it as a function
add_id_origin.on_click(path_origin_button_clicked)

add_id_destin.on_click(path_destin_button_clicked)

clear_origin_ids.on_click(origin_button_clear)

clear_destin_ids.on_click(destin_button_clear)

# ------ TO DISPLAY -------

display(select_origin_id)
display(select_destin_id)

display(add_id_origin)
display(add_id_destin)

display(clear_origin_ids)
display(clear_destin_ids)

display(o_out)
display(d_out)

Combobox(value='', description='OriginID', ensure_option=True, options=('5785640', '5785641', '5785642', '5785…

Combobox(value='', description='DestinationID', ensure_option=True, options=('5785640', '5785641', '5785642', …

Button(button_style='info', description='Add OriginID', icon='check', style=ButtonStyle(), tooltip='Click me')

Button(button_style='info', description='Add DestinationID', icon='check', style=ButtonStyle(), tooltip='Click…

Button(button_style='danger', description='Clear Origin(s)', icon='remove', style=ButtonStyle(), tooltip='Clic…

Button(button_style='danger', description='Clear Destin(s)', icon='remove', style=ButtonStyle(), tooltip='Clic…

Output()

Output()

#### ***Choose Network Type***

In [59]:
# a list with the network types
# network_type "all_private", "all", "bike", "drive", "drive_service", "walk"
network_type = [('All Networks','all'), 
                ('Bike Paths Network','bike'), 
                ('Road Network','drive'), 
                ('Walk Paths Network', 'walk')]

color_path_map = [('Viridis    #Sequential change','viridis'), 
                 ('Yellow - Green - Blue    #Sequential change','YlGnBu'),
                 ('Turquese - Purple    #Sequential change', 'cool')]

# ---------------------------------------------------------------------------

# adding the widget to get information of Network
select_network_button = widgets.Dropdown(placeholder='Select Path Network', 
                                 options=network_type, description='Path Network',
                                 value = 'drive',
                                 ensure_option=True, 
                                 disabled=False)

map_path_button = widgets.Button(description='Find Shortest Path', 
                                 disabled=False, 
                                 button_style='success', 
                                 tooltip='Click me', 
                                 icon='map')

color_path_button = widgets.Dropdown(placeholder='Select a color map', 
                                     options = color_path_map, description='Route Cmap:',
                                     value = 'cool',
                                     ensure_option=True, 
                                     disabled=False)

shp_path_button = widgets.Button(description='Save Routes SHP',
                                 disabled=False,
                                 button_style='primary',
                                 tooltip='Click me', 
                                 icon='download')
                        
png_path_button = widgets.Button(description='Save Map PNG',
                                 disabled=False,
                                 button_style='primary',
                                 tooltip='Click me', 
                                 icon='download')

# ---------------------------------------------------------------------------

path_out = widgets.Output()

# create event on click
map_path_button.on_click(map_shortest_path)
shp_path_button.on_click(shp_shortest_path)
png_path_button.on_click(png_shortest_path)

# ------ TO DISPLAY -------
display(select_network_button)
display(color_path_button)

display(map_path_button)
display(shp_path_button)
display(png_path_button)


display(path_out)

Dropdown(description='Path Network', index=2, options=(('All Networks', 'all'), ('Bike Paths Network', 'bike')…

Dropdown(description='Route Cmap:', index=2, options=(('Viridis    #Sequential change', 'viridis'), ('Yellow -…

Button(button_style='success', description='Find Shortest Path', icon='map', style=ButtonStyle(), tooltip='Cli…

Button(button_style='primary', description='Save Routes SHP', icon='download', style=ButtonStyle(), tooltip='C…

Button(button_style='primary', description='Save Map PNG', icon='download', style=ButtonStyle(), tooltip='Clic…

Output()

### ***YKR ID Explorer***
________________________
Here you can explore the YKR IDs of the Travel Time Matrix of Helsinki Region. 

In [60]:
# -----------------------------------------------------------------------------
#                                   FUNCTIONS
# -----------------------------------------------------------------------------

def grid_codes(feature):
    '''Def which gives back a Style Color
    :param
    - feature <feature> Defined feature already. No need eto specify inside GeoJson Folium
    :return
    <dictionary> with style colors
    '''

    YKR_grid = low_series.get(int(feature['id']), None)

    return {'fillColor': 'black',
            'color': 'black',
            'weight': 1,
            'fillOpacity': 0,
            'opacity': 0.4}

In [61]:
# including an ID for Folium
grid['geoid'] = grid.index.astype(str)

# creating a map instance visualize the grid
m = folium.Map(width=700, height=500, location=[60.25, 24.85], zoom_start=10, control_scale=True)

# setting a series that will be used in Style Function
low_series = grid.set_index('geoid')

# creating a GeoJson of the Grid Features and adding to the map instance
grid_gjson = folium.features.GeoJson(grid, name='YKR_Grid', style_function=grid_codes,
                                     tooltip=folium.features.GeoJsonTooltip(fields=['YKR_ID'],
                                             aliases = ['YKR Identifier'],
                                             labels=True,
                                             sticky=True))
grid_gjson.add_to(m);

In [62]:
m